In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn
from sklearn.metrics import mean_squared_error, mean_absolute_error
from sklearn.metrics import r2_score
import warnings
warnings.filterwarnings('ignore')

from pmdarima import auto_arima
from statsmodels.tsa.arima.model import ARIMA
from statsmodels.tsa.statespace.sarimax import SARIMAX
from statsmodels.tsa.holtwinters import ExponentialSmoothing

import darts
from darts import TimeSeries
from darts.models import NBEATSModel
from darts.dataprocessing.transformers import Scaler, MissingValuesFiller
from darts.metrics import mape as mape_darts
from darts.metrics import r2_score as r2_score_darts
from darts.datasets import AirPassengersDataset

from sklearn.ensemble import RandomForestRegressor

import logging
import mlflow

In [2]:
def mape_score(y_test, pred):
    y_test, pred = np.array(y_test), np.array(pred)
    mape = np.mean(np.abs((y_test - pred) / y_test)) * 100
    return mape

In [3]:
def metrics(test, pred):
    d= {}
    mse = mean_squared_error(test, pred)
    rmse = np.sqrt(mse)
    # r_squared = r2_score(test, pred)
    mape= mape_score(test, pred)
    mae = mean_absolute_error(test, pred)

    d['MSE'] = mse
    d['RMSE'] = rmse
    # d['R-squared'] = r_squared
    d['MAPE'] = mape
    d['MAE'] = mae
    
    return d

In [4]:
path_imp = r'C:\Users\himanshu.verma\vs_code\POC_MGC\Dataset\sku_start_end_imputed.csv'

df_sku_imp = pd.read_csv(path_imp)
df_sku_imp.head()

DATE  VOLUME_MT_ACT  NET_REVENUE_ACT  GROSS_PROFIT_ACT  \
0  2020-01-01        8.18452     42289.702167      20821.292171   
1  2020-02-01        8.63388     44417.594186      21621.080942   
2  2020-03-01        6.51811     33395.663947      16100.447084   
3  2020-04-01        6.14640     32161.846809      11078.329210   
4  2020-05-01        2.20229     11865.758646       1940.323139   

                                        CODE COUNTRY CLUSTER_SUB_CHANNEL  \
0  Bakeries_Kuwait_Grocery/Retail_4004015437  Kuwait      Grocery/Retail   
1  Bakeries_Kuwait_Grocery/Retail_4004015437  Kuwait      Grocery/Retail   
2  Bakeries_Kuwait_Grocery/Retail_4004015437  Kuwait      Grocery/Retail   
3  Bakeries_Kuwait_Grocery/Retail_4004015437  Kuwait      Grocery/Retail   
4  Bakeries_Kuwait_Grocery/Retail_4004015437  Kuwait      Grocery/Retail   

   CATEGORY  
0  Bakeries  
1  Bakeries  
2  Bakeries  
3  Bakeries  
4  Bakeries

In [5]:
pd.set_option('display.max_rows', None)
df_sku_grouped = df_sku_imp.groupby(['CATEGORY', 'CODE'])['NET_REVENUE_ACT'].sum().reset_index().sort_values(by= 'NET_REVENUE_ACT', ascending= False)
df_sku_grouped.head()

CATEGORY                                     CODE  NET_REVENUE_ACT
79           CPG                 CPG_Egypt_OutofScope_CPG     1.018067e+09
250  Frozen Veg.       FrozenVeg._Egypt_HORECA_4094016015     2.155766e+07
256  Frozen Veg.  FrozenVeg._UAE_AMRestaurants_4094026027     1.931843e+07
594      Protein         Protein_KSA_Wholesale_4001370861     1.901816e+07
243  Frozen Veg.  FrozenVeg._Egypt_Distributor_4094016015     1.672102e+07

In [6]:
d = {}

d['CPG'] = 'CPG_Egypt_OutofScope_CPG'
d['Frozen Veg.'] = 'FrozenVeg._Egypt_HORECA_4094016015'
d['Protein'] = 'Protein_KSA_Wholesale_4001370861'
d['C&W'] = 'C&W_KSA_Distributor_4040413001'
d['Kwt Agencies'] = 'KwtAgencies_Kuwait_Grocery/Retail_5006460550'
d['Bakeries'] = 'Bakeries_Kuwait_ModernTrade_4004015437'
d['Frozen Veg-Meat'] = 'FrozenVeg-Meat_KSA_Wholesale_5011390105'
d['Cake'] = 'Cake_KSA_SupplyChainLed_3040431840'

d.values()

dict_values(['CPG_Egypt_OutofScope_CPG', 'FrozenVeg._Egypt_HORECA_4094016015', 'Protein_KSA_Wholesale_4001370861', 'C&W_KSA_Distributor_4040413001', 'KwtAgencies_Kuwait_Grocery/Retail_5006460550', 'Bakeries_Kuwait_ModernTrade_4004015437', 'FrozenVeg-Meat_KSA_Wholesale_5011390105', 'Cake_KSA_SupplyChainLed_3040431840'])

In [7]:
# best_nbeats_sku = 'Protein_KSA_Wholesale_4001370861'

In [8]:
df_test = df_sku_imp.copy()

print(len(df_test[df_test['CODE'] == 'Protein_KSA_Wholesale_4001370861']))
df_test = df_test[df_test['CODE'] == 'Protein_KSA_Wholesale_4001370861'][['DATE', 'VOLUME_MT_ACT', 'CODE']]



df_test['DATE'] = pd.to_datetime(df_test['DATE'])
df_test.set_index(['DATE'], inplace= True)

df_test.sort_index(inplace= True)
df_test.head()

39


VOLUME_MT_ACT                              CODE
DATE                                                       
2020-01-01        56.5400  Protein_KSA_Wholesale_4001370861
2020-02-01        74.8670  Protein_KSA_Wholesale_4001370861
2020-03-01       124.4970  Protein_KSA_Wholesale_4001370861
2020-04-01        49.3603  Protein_KSA_Wholesale_4001370861
2020-05-01        80.3630  Protein_KSA_Wholesale_4001370861

In [14]:
def models(df_new):
    
    sku_name = df_new['CODE']
    df = df_new.drop(columns= ['CODE'])
    print(df.head())
     
    exp_id = mlflow.set_experiment(experiment_name= 'SKU_all')
    with mlflow.start_run(experiment_id= exp_id.experiment_id):   
    

        model_autoarima = auto_arima(df['VOLUME_MT_ACT'], seasonal=True, stepwise=True, suppress_warnings=True, max_order=None)

        p, d, q = model_autoarima.order
        print(f'Best ARIMA Order: ({p}, {d}, {q})')
        
        train_new = df[:-6]
        test_new = df[-6:]
        
        model_arima_new = ARIMA(train_new, order=(p, d, q))
        results_arima_new = model_arima_new.fit()

        # 1. Make forecasts using the fitted ARIMA model
        forecast_arima = results_arima_new.forecast(steps=6)
        
        forecast_arima.index= test_new.index

        df_arima_new_pred = pd.DataFrame(forecast_arima)
        df_arima_test_new = pd.DataFrame(test_new)

        df_arima_new_data = pd.concat([df_arima_test_new, df_arima_new_pred], axis= 1)
        print(f'1. ARIMA model output : {df_arima_new_data}')
        
        print('\n')
        
        # metrics_arima
        
        arima_metrics = []
        arima_metrics.append(metrics(df_arima_new_data['VOLUME_MT_ACT'], df_arima_new_data['predicted_mean']))
        print(f'ARIMA metrics : {arima_metrics}')
        # print('\n')
        # print('--------------------------------------------------')
        # print('\n')
        
        # 2. SARIMAX
        model_sarima = SARIMAX(train_new, order=(p, d, q), seasonal_order=(p, d, q, 12), random_state= 90)
        results_sarima = model_sarima.fit()


        forecast_sarima = results_sarima.get_forecast(steps=6)
        forecast_mean = forecast_sarima.predicted_mean
        
        forecast_mean.index= test_new.index

        forecast_mean= pd.DataFrame(forecast_mean)
        test_new= pd.DataFrame(test_new)

        df_sarimax = pd.concat([test_new, forecast_mean], axis= 1)
        print(f'2. SARIMAX model output : {df_sarimax}')
        print('\n')
        
        
        # metrics_sarimax

        sarimax_metrics = []
        sarimax_metrics.append(metrics(df_sarimax['VOLUME_MT_ACT'], df_sarimax['predicted_mean']))
        
        print(f'SARIMAX metrics : {sarimax_metrics}')
        # print('\n')
        # print('--------------------------------------------------')
        # print('\n')
        
        # 3. Holt's Winter
        model_holt_new = ExponentialSmoothing(train_new, trend= 'add', seasonal= 'add').fit()
        
        test_holt_new = model_holt_new.forecast(6)

        test_holt_new = pd.DataFrame(test_holt_new)
        test_holt_new.rename(columns= {0: 'pred_holt_new'}, inplace= True)
        test_holt_new

        df_holt_new_pred = pd.DataFrame(test_holt_new)
        df_test_holt_new = pd.DataFrame(test_new)

        df_holt_new_pred.index= df_test_holt_new.index
        df_holt_new=  pd.concat([df_holt_new_pred, df_test_holt_new], axis= 1)
        print(f'3. Holt Winter model output : {df_holt_new}')
        print('\n')
        
        
        # Metrics_holt

        holt_metrics = []
        holt_metrics.append(metrics(df_holt_new['VOLUME_MT_ACT'], df_holt_new['pred_holt_new']))
        print(f'Holt Winter metrics : {holt_metrics}')
        # print('\n')
        # print('--------------------------------------------------')
        # print('\n')
        
        
        # 4. N-Beats
        
        df_nbeats = df.copy()

        # data_nbeats_new = pd.DataFrame(data_nbeats_new)
        data_nbeats_new = df_nbeats.reset_index()
        data_nbeats_new = data_nbeats_new.rename(columns= {'index': 'DATE'})

        # Create a TimeSeries, specifying the time and value columns
        series_new = TimeSeries.from_dataframe(data_nbeats_new, 'DATE', 'VOLUME_MT_ACT')
        series_new.pd_dataframe()
        
        print('\n')
        print(f'Series_new : {len(series_new)}')
        train_nbeats_new, val_nbeats_new = series_new.split_after(pd.Timestamp("20220901"))
        print(f'Train_nbeats_new : {len(train_nbeats_new)}')
        print(f'Val_nbeats_new : {len(val_nbeats_new)}')
        print('\n')
        
        model_nbeats_new = NBEATSModel(
        input_chunk_length= 12,
        output_chunk_length=2,
        generic_architecture=True,
        num_stacks=5,
        num_blocks=5,
        num_layers=5,
        layer_widths= 150,
        n_epochs= 50,
        batch_size= 2,
        model_name="nbeats_run",
        random_state= 90
        )

        results_nbeats_new= model_nbeats_new.fit(series= train_nbeats_new, verbose= False)
        
        ts_tpred_new = results_nbeats_new.predict(n= 6,  
                                # past_covariates=cov_t,
                                num_samples= 1,   
                                n_jobs= -1, 
                                verbose=False)
        
        nbeats_pred_new = pd.DataFrame(ts_tpred_new.pd_dataframe())
        nbeats_pred_new.rename(columns= {'VOLUME_MT_ACT': 'nbeats_pred_new'}, inplace= True)
        
        df_nbeats_new = pd.concat([val_nbeats_new.pd_dataframe(), nbeats_pred_new], axis=1)
        print(f'4. NBeats model output : {df_nbeats_new}')
        print('\n')
        
        # metrics_nbeats
        nbeats_metrics = []
        nbeats_metrics.append(metrics(df_nbeats_new['VOLUME_MT_ACT'], df_nbeats_new['nbeats_pred_new']))
        print(f'NBEATS metrics : {nbeats_metrics}')
        # print('\n')
        # print('--------------------------------------------------')
        # print('\n')
        
        
        # 5. Random Forest Regressor
        
        df_rf = df_test.copy()
        df_rf.head()


        # Differencing the time series

        df_rf['lag_1'] = df_rf['VOLUME_MT_ACT'].shift(1)
        df_rf['lag_2'] = df_rf['VOLUME_MT_ACT'].shift(2)
        df_rf['lag_3'] = df_rf['VOLUME_MT_ACT'].shift(3)
        # df_rf['lag_4'] = df_rf['VOLUME_MT_ACT'].shift(4)
        # df_rf['lag_5'] = df_rf['VOLUME_MT_ACT'].shift(5)
        # df_rf['lag_6'] = df_rf['VOLUME_MT_ACT'].shift(6)
        # df_rf['lag_7'] = df_rf['VOLUME_MT_ACT'].shift(7)
        # df_rf['lag_8'] = df_rf['VOLUME_MT_ACT'].shift(8)
        # df_rf['lag_9'] = df_rf['VOLUME_MT_ACT'].shift(9)
        # df_rf['lag_10'] = df_rf['VOLUME_MT_ACT'].shift(10)
        # df_rf['lag_11'] = df_rf['VOLUME_MT_ACT'].shift(11)
        # df_rf['lag_12'] = df_rf['VOLUME_MT_ACT'].shift(12)
        # df_rf['lag_13'] = df_rf['VOLUME_MT_ACT'].shift(13)
        
        # 'lag_6', 'lag_7', 'lag_8', 'lag_9', 'lag_10', 'lag_11', 'lag_12', 'lag_13'

        df_rf = df_rf.dropna()
        df_rf = df_rf[['VOLUME_MT_ACT', 'lag_1', 'lag_2', 'lag_3']]

        # df_rf, len(df_rf)
        X = df_rf.drop(columns= ['VOLUME_MT_ACT'], axis=1)
        y = df_rf['VOLUME_MT_ACT']

        X_train_rf, X_test_rf, y_train_rf, y_test_rf = X[:-6], X[-6:], y[:-6], y[-6:]
        
        model_rf= RandomForestRegressor(random_state= 100)

        model_rf.fit(X_train_rf, y_train_rf)
        pred_rf = model_rf.predict(X_test_rf)
        
        pred_rf = pd.DataFrame(pred_rf, index= y_test_rf.index)
        df_rf = pd.concat([y_test_rf, pred_rf], axis=1)

        df_rf.columns = ['actual', 'prediction']
        
        print(f'5. Random Forest model output : {df_rf}')
        print('\n')
        
        # metrics_rf
        
        rf_metrics = []
        rf_metrics.append(metrics(df_rf['actual'], df_rf['prediction']))
        print(f'Random forest metrics : {rf_metrics}')
        # print('\n')
        # print('--------------------------------------------------')
        # print('\n')
        
        # print('--------------------------------------------------')
        # print('--------------------------------------------------')
        print('FINAL METRICS : ')
        print(f'1. ARIMA metrics : {arima_metrics}')
        print(f'2. SARIMAX metrics : {sarimax_metrics}')
        print(f'3. Holt Winter metrics : {holt_metrics}')
        print(f'4. NBEATS metrics : {nbeats_metrics}')
        print(f'5. Random Forest metrics : {rf_metrics}')
        # print('--------------------------------------------------')
        # print('--------------------------------------------------')
        
        mlflow.log_param('SKU_name', sku_name)
        mlflow.log_param('ARIMA_metrics', arima_metrics)
        mlflow.log_param('SARIMAX_metrics', sarimax_metrics)
        mlflow.log_param('Holt_Winter_metrics', holt_metrics)
        mlflow.log_param('NBEATS_metrics', nbeats_metrics)
        mlflow.log_param('Random_Forest_metrics', rf_metrics)
    
    

In [10]:
# For a single SKU (BEST NBEATS SKU)

# models(df_test)

2023/11/06 14:37:04 INFO mlflow.tracking.fluent: Experiment with name 'best_sku_revenue' does not exist. Creating a new experiment.


            VOLUME_MT_ACT
DATE                     
2020-01-01        56.5400
2020-02-01        74.8670
2020-03-01       124.4970
2020-04-01        49.3603
2020-05-01        80.3630
Best ARIMA Order: (0, 0, 1)
1. ARIMA model output :             VOLUME_MT_ACT  predicted_mean
DATE                                     
2022-10-01        184.051      100.628992
2022-11-01         77.998      127.553499
2022-12-01         77.870      127.553499
2023-01-01        139.062      127.553499
2023-02-01        124.251      127.553499
2023-03-01        182.247      127.553499


ARIMA metrics : [{'MSE': 2503.026673500703, 'RMSE': 50.03025757979568, 'MAPE': 35.60121890215555, 'MAE': 42.027584418832475}]
2. SARIMAX model output :             VOLUME_MT_ACT  predicted_mean
DATE                                     
2022-10-01        184.051       -2.901499
2022-11-01         77.998        2.185663
2022-12-01         77.870      103.161609
2023-01-01        139.062      132.019457
2023-02-01        124.25

c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\ba

4. NBeats model output : component   VOLUME_MT_ACT  nbeats_pred_new
DATE                                      
2022-10-01        184.051       204.594987
2022-11-01         77.998        93.404840
2022-12-01         77.870        62.295209
2023-01-01        139.062        96.503451
2023-02-01        124.251       165.098873
2023-03-01        182.247       186.546969


NBEATS metrics : [{'MSE': 733.3781328825927, 'RMSE': 27.080955169317658, 'MAPE': 19.4591189988395, 'MAE': 23.205334933407965}]
5. Random Forest model output :              actual  prediction
DATE                           
2022-10-01  184.051   92.161031
2022-11-01   77.998  209.385661
2022-12-01   77.870   83.941376
2023-01-01  139.062  100.810385
2023-02-01  124.251  132.030534
2023-03-01  182.247  152.791142


Random forest metrics : [{'MSE': 4689.116705997869, 'RMSE': 68.47712542154402, 'MAPE': 46.01730600068697, 'MAE': 50.80600226644958}]
FINAL METRICS : 
1. ARIMA metrics : [{'MSE': 2503.026673500703, 'RMSE': 50.0302

In [53]:
for i in d.values():
    print(i)

CPG_Egypt_OutofScope_CPG
FrozenVeg._Egypt_HORECA_4094016015
Protein_KSA_Wholesale_4001370861
C&W_KSA_Distributor_4040413001
KwtAgencies_Kuwait_Grocery/Retail_5006460550
Bakeries_Kuwait_ModernTrade_4004015437
FrozenVeg-Meat_KSA_Wholesale_5011390105
Cake_KSA_SupplyChainLed_3040431840


In [54]:
sdgSW

NameError: name 'sdgSW' is not defined

### Logging the results of SKU_present in dictionary 'd'

In [13]:
# df_test_dict = pd.read_csv(path_imp)

# l = []
# for code in d.values():
#     l.append(code)
    

# # print(l)
# for i in l:
#     print(i)
    
#     df_dict = df_test_dict[df_test_dict['CODE'] == i][['DATE', 'VOLUME_MT_ACT', 'CODE']]
    
#     df_dict['DATE'] = pd.to_datetime(df_dict['DATE'])
#     df_dict.set_index(['DATE'], inplace= True)

#     df_dict.sort_index(inplace= True)
#     models(df_dict)

2023/11/06 14:38:49 INFO mlflow.tracking.fluent: Experiment with name 'SKU_in_dict' does not exist. Creating a new experiment.


CPG_Egypt_OutofScope_CPG
            VOLUME_MT_ACT
DATE                     
2020-01-01    21650.25000
2020-02-01    22691.00000
2020-03-01    29598.85251
2020-04-01    24399.56083
2020-05-01    24491.01261


c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\ba

Best ARIMA Order: (0, 1, 0)
1. ARIMA model output :             VOLUME_MT_ACT  predicted_mean
DATE                                     
2022-10-01   22980.470639    22602.866381
2022-11-01   18751.332699    22602.866381
2022-12-01   15978.480552    22602.866381
2023-01-01   17540.660000    22602.866381
2023-02-01   18369.570000    22602.866381
2023-03-01   22875.265220    22602.866381


ARIMA metrics : [{'MSE': 17080052.8519016, 'RMSE': 4132.802058156379, 'MAPE': 19.456195913366802, 'MAE': 3403.5708950000003}]
2. SARIMAX model output :             VOLUME_MT_ACT  predicted_mean
DATE                                     
2022-10-01   22980.470639    25277.436405
2022-11-01   18751.332699    19643.813230
2022-12-01   15978.480552    17275.270879
2023-01-01   17540.660000    17925.904792
2023-02-01   18369.570000    19532.328869
2023-03-01   22875.265220    21375.130280


SARIMAX metrics : [{'MSE': 1917510.8260001382, 'RMSE': 1384.7421514491925, 'MAPE': 6.325784067535888, 'MAE': 1255.729204

`Trainer.fit` stopped: `max_epochs=50` reached.
GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


...

4. NBeats model output : component   VOLUME_MT_ACT  nbeats_pred_new
DATE                                      
2022-10-01        28.7200       225.739880
2022-11-01        92.8100       106.455911
2022-12-01       239.9350       235.654894
2023-01-01       132.2175        86.320125
2023-02-01       114.4800       167.597903
2023-03-01        73.0400       242.257219


NBEATS metrics : [{'MSE': 12097.318514376211, 'RMSE': 109.98781075362947, 'MAPE': 169.21326293763786, 'MAE': 80.52973232806755}]
5. Random Forest model output :              actual  prediction
DATE                           
2022-10-01  184.051   92.161031
2022-11-01   77.998  209.385661
2022-12-01   77.870   83.941376
2023-01-01  139.062  100.810385
2023-02-01  124.251  132.030534
2023-03-01  182.247  152.791142


Random forest metrics : [{'MSE': 4689.116705997869, 'RMSE': 68.47712542154402, 'MAPE': 46.01730600068697, 'MAE': 50.80600226644958}]
FINAL METRICS : 
1. ARIMA metrics : [{'MSE': 4289.864741176431, 'RMSE': 65.49

c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\ba

Best ARIMA Order: (0, 0, 1)
1. ARIMA model output :             VOLUME_MT_ACT  predicted_mean
DATE                                     
2022-10-01        10.9242        9.844768
2022-11-01         8.3448        8.926906
2022-12-01        10.8270        8.926906
2023-01-01         9.1530        8.926906
2023-02-01         9.6372        8.926906
2023-03-01        10.5192        8.926906


ARIMA metrics : [{'MSE': 1.3675690311798705, 'RMSE': 1.1694310715813354, 'MAPE': 9.897315632280804, 'MAE': 1.0150523165112808}]
2. SARIMAX model output :             VOLUME_MT_ACT  predicted_mean
DATE                                     
2022-10-01        10.9242       -6.016415
2022-11-01         8.3448        1.272884
2022-12-01        10.8270        1.358457
2023-01-01         9.1530        3.755134
2023-02-01         9.6372        3.575170
2023-03-01        10.5192        4.178668


SARIMAX metrics : [{'MSE': 88.78954475298956, 'RMSE': 9.422820424532643, 'MAPE': 84.90426376419396, 'MAE': 8.546917187

`Trainer.fit` stopped: `max_epochs=50` reached.
GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


4. NBeats model output : component   VOLUME_MT_ACT  nbeats_pred_new
DATE                                      
2022-10-01        10.9242         7.767831
2022-11-01         8.3448        12.818912
2022-12-01        10.8270        11.487639
2023-01-01         9.1530        15.512325
2023-02-01         9.6372         7.748197
2023-03-01        10.5192        11.722717


NBEATS metrics : [{'MSE': 12.645764968168004, 'RMSE': 3.556088436494234, 'MAPE': 31.521842122850202, 'MAE': 2.9571608275548336}]
5. Random Forest model output :              actual  prediction
DATE                           
2022-10-01  184.051   92.161031
2022-11-01   77.998  209.385661
2022-12-01   77.870   83.941376
2023-01-01  139.062  100.810385
2023-02-01  124.251  132.030534
2023-03-01  182.247  152.791142


Random forest metrics : [{'MSE': 4689.116705997869, 'RMSE': 68.47712542154402, 'MAPE': 46.01730600068697, 'MAE': 50.80600226644958}]
FINAL METRICS : 
1. ARIMA metrics : [{'MSE': 1.3675690311798705, 'RMSE': 1.16

## Metrics for all the 'SKUs'

In [15]:
all_codes = list(df_sku_imp['CODE'].unique())


df_test_all = pd.read_csv(path_imp)

# l = []
# for code in d.values():
#     l.append(code)

# print(l)

for i in all_codes:
    print('\n')
    print(f'SKU CODE -----> {i}')
    print('\n')
    
    df_all = df_test_all[df_test_all['CODE'] == i][['DATE', 'VOLUME_MT_ACT', 'CODE']]
    df_all['DATE'] = pd.to_datetime(df_all['DATE'])
    df_all.set_index(['DATE'], inplace= True)

    df_all.sort_index(inplace= True)
    models(df_all)

2023/11/06 14:45:20 INFO mlflow.tracking.fluent: Experiment with name 'SKU_all' does not exist. Creating a new experiment.




SKU CODE -----> Bakeries_Kuwait_Grocery/Retail_4004015437


            VOLUME_MT_ACT
DATE                     
2020-01-01        8.18452
2020-02-01        8.63388
2020-03-01        6.51811
2020-04-01        6.14640
2020-05-01        2.20229
Best ARIMA Order: (1, 0, 0)
1. ARIMA model output :             VOLUME_MT_ACT  predicted_mean
DATE                                     
2022-10-01       9.670109        7.792410
2022-11-01       9.163503        7.919134
2022-12-01       8.301675        7.961429
2023-01-01       2.378436        7.975544
2023-02-01       8.290474        7.980255
2023-03-01       8.878632        7.981828


ARIMA metrics : [{'MSE': 6.236348362051479, 'RMSE': 2.497268179842021, 'MAPE': 47.71092474996385, 'MAE': 1.7110742466255597}]
2. SARIMAX model output :             VOLUME_MT_ACT  predicted_mean
DATE                                     
2022-10-01       9.670109        7.491134
2022-11-01       9.163503       11.274109
2022-12-01       8.301675        5.121048
2023

c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\ba

4. NBeats model output : component   VOLUME_MT_ACT  nbeats_pred_new
DATE                                      
2022-10-01       9.670109        13.093616
2022-11-01       9.163503        12.475431
2022-12-01       8.301675        14.926279
2023-01-01       2.378436        11.366623
2023-02-01       8.290474        27.599983
2023-03-01       8.878632        11.480599


NBEATS metrics : [{'MSE': 87.83159134079854, 'RMSE': 9.371851009314998, 'MAPE': 131.91087012969226, 'MAE': 7.37661723900155}]
5. Random Forest model output :              actual  prediction
DATE                           
2022-10-01  184.051   92.161031
2022-11-01   77.998  209.385661
2022-12-01   77.870   83.941376
2023-01-01  139.062  100.810385
2023-02-01  124.251  132.030534
2023-03-01  182.247  152.791142


Random forest metrics : [{'MSE': 4689.116705997869, 'RMSE': 68.47712542154402, 'MAPE': 46.01730600068697, 'MAE': 50.80600226644958}]
FINAL METRICS : 
1. ARIMA metrics : [{'MSE': 6.236348362051479, 'RMSE': 2.497268

c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\ba

...

4. NBeats model output : component   VOLUME_MT_ACT  nbeats_pred_new
DATE                                      
2022-10-01       3.573335         2.766520
2022-11-01       3.057432         3.511064
2022-12-01       3.521203         1.756302
2023-01-01       4.203770         2.542101
2023-02-01       2.603213         3.895599
2023-03-01       4.757580         4.560904


NBEATS metrics : [{'MSE': 1.4069495478688159, 'RMSE': 1.1861490411701288, 'MAPE': 30.14095202751172, 'MAE': 1.0293465833602793}]
5. Random Forest model output :              actual  prediction
DATE                           
2022-10-01  184.051   92.161031
2022-11-01   77.998  209.385661
2022-12-01   77.870   83.941376
2023-01-01  139.062  100.810385
2023-02-01  124.251  132.030534
2023-03-01  182.247  152.791142


Random forest metrics : [{'MSE': 4689.116705997869, 'RMSE': 68.47712542154402, 'MAPE': 46.01730600068697, 'MAE': 50.80600226644958}]
FINAL METRICS : 
1. ARIMA metrics : [{'MSE': 0.7243034931836457, 'RMSE': 0.85

c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  self._init_dates(dates, freq)
c:\Users\himanshu.verma\anaconda3\envs\time_env\Lib\site-packages\statsmodels\tsa\ba

2. SARIMAX model output :             VOLUME_MT_ACT  predicted_mean
DATE                                     
2022-10-01       2.132500        2.626286
2022-11-01       1.935000        1.452817
2022-12-01       2.482500        2.647650
2023-01-01       3.980812        5.166783
2023-02-01       2.190000        3.979517
2023-03-01       4.050000        2.641777


SARIMAX metrics : [{'MSE': 1.1825983891272582, 'RMSE': 1.0874733969744999, 'MAPE': 33.5005207372389, 'MAE': 0.9208051560854651}]
3. Holt Winter model output :             pred_holt_new  VOLUME_MT_ACT
DATE                                    
2022-10-01       1.831485       2.132500
2022-11-01       1.355822       1.935000
2022-12-01       2.049642       2.482500
2023-01-01       3.362760       3.980812
2023-02-01       2.567760       2.190000
2023-03-01       2.440262       4.050000


Holt Winter metrics : [{'MSE': 0.6215619833244055, 'RMSE': 0.7883920238843145, 'MAPE': 22.33423400861335, 'MAE': 0.6531003764165619}]


Series_new 

`Trainer.fit` stopped: `max_epochs=50` reached.
GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


4. NBeats model output : component   VOLUME_MT_ACT  nbeats_pred_new
DATE                                      
2022-10-01       2.132500         1.992797
2022-11-01       1.935000         0.960241
2022-12-01       2.482500         1.822781
2023-01-01       3.980812         2.840275
2023-02-01       2.190000         1.799961
2023-03-01       4.050000         2.838663


NBEATS metrics : [{'MSE': 0.7208658031669755, 'RMSE': 0.8490381635515423, 'MAPE': 26.64524733533826, 'MAE': 0.752682373591839}]
5. Random Forest model output :              actual  prediction
DATE                           
2022-10-01  184.051   92.161031
2022-11-01   77.998  209.385661
2022-12-01   77.870   83.941376
2023-01-01  139.062  100.810385
2023-02-01  124.251  132.030534
2023-03-01  182.247  152.791142


Random forest metrics : [{'MSE': 4689.116705997869, 'RMSE': 68.47712542154402, 'MAPE': 46.01730600068697, 'MAE': 50.80600226644958}]
FINAL METRICS : 
1. ARIMA metrics : [{'MSE': 2.6560930437416306, 'RMSE': 1.629